In [1]:
from hct.envs.low_level_env import LowLevelEnv
from hct.envs.ant_test import AntTest
from hct.envs.tools import world_to_relative, timeit

import functools
import jax
import os
import time

from datetime import datetime
from jax import numpy as jp
import matplotlib.pyplot as plt

from IPython.display import HTML, clear_output

import brax

from brax.envs.humanoid import Humanoid
from brax.envs.humanoidstandup import HumanoidStandup
import flax
from brax import envs
from brax import base
from brax.io import model
from brax.io import json
from brax.io import html
from hct.training import train as ppo
from brax.training.agents.sac import train as sac
from brax.base import Transform, Motion
from brax.math import euler_to_quat
from absl import logging

from brax.envs.ant import Ant

import getpass
import socket

from brax.kinematics import world_to_joint, inverse, forward

env=LowLevelEnv()


2023-07-25 15:36:20.375619: E external/xla/xla/stream_executor/cuda/cuda_driver.cc:268] failed call to cuInit: CUDA_ERROR_NO_DEVICE: no CUDA-capable device is detected
No GPU/TPU found, falling back to CPU. (Set TF_CPP_MIN_LOG_LEVEL=0 and rerun for more info.)


In [2]:
res = env.test(iterations=50)

Time to JIT 'reset': 8.314652681350708 seconds
Time to JIT 'step': 12.77626895904541 seconds
Time to call 'reset' after JIT compilation: 0.0004069614410400391 seconds
Time to call 'step' after JIT compilation: 0.0008060073852539063 seconds


In [9]:
for s in res[3]:

    goal = s.info['goal']

    # Take action
    pipeline_state = s.pipeline_state

    # Check if unhealthy
    min_z, max_z = env._healthy_z_range
    is_unhealthy = jp.where(pipeline_state.x.pos[0, 2] < min_z, x=1.0, y=0.0)
    is_unhealthy = jp.where(
        pipeline_state.x.pos[0, 2] > max_z, x=1.0, y=is_unhealthy
    )

    # Compute goal distance
    goal_distance = env._goal_dist(pipeline_state, goal, frame = 'relative')/env.max_goal_dist

    # Check if goal reached
    goal_reached = jp.where(
      goal_distance < env.goal_distance_epsilon, x=1.0, y=0.0
    )

    # Compute state observation
    done = 0 + jp.logical_or(is_unhealthy, goal_reached)

    print(done)

0
0
0
0
0
0
0
0
0
0
0
0


0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0


In [6]:
from hct.envs.tools import goal_to_state
goals = [goal_to_state(s.info['goal'], env.sys) for s in res[2]]


In [7]:
print(html.render(env.sys, goals))

<!DOCTYPE html>
<html>

  <head>
    <title>Brax visualizer</title>
    <link rel="shortcut icon" type="image/x-icon" href="/favicon.ico">
  </head>

  <style>
    body {
      margin: 0;
      padding: 0;
    }

    #brax-viewer {
      height: 480px;
      margin: 0;
      padding: 0;
    }
  </style>
  <script async src="https://unpkg.com/es-module-shims@1.6.3/dist/es-module-shims.js"></script>

  <script type="importmap">
    {
      "imports": {
        "three": "https://unpkg.com/three@0.150.1/build/three.module.js",
        "three/addons/": "https://unpkg.com/three@0.150.1/examples/jsm/",
        "lilgui": "https://cdn.jsdelivr.net/npm/lil-gui@0.18.0/+esm",
        "viewer": "https://cdn.jsdelivr.net/gh/google/brax@v0.9.1/brax/visualizer/js/viewer.js"
      }
    }
  </script>

  <script type="application/javascript">
  var system = {"dt": 0.009999999776482582, "gravity": [0.0, 0.0, -9.8100004196167], "viscosity": 0.0, "density": 0.0, "link": {"transform": {"pos": [[0.0, 0.0, 0.

In [1]:
import logging

logging.basicConfig(level=logging.INFO)
import training


2023-07-24 22:10:13.588739: E external/xla/xla/stream_executor/cuda/cuda_driver.cc:268] failed call to cuInit: CUDA_ERROR_NO_DEVICE: no CUDA-capable device is detected
INFO:jax._src.xla_bridge:Unable to initialize backend 'cuda': FAILED_PRECONDITION: No visible GPU devices.
INFO:jax._src.xla_bridge:Unable to initialize backend 'rocm': NOT_FOUND: Could not find registered platform with name: "rocm". Available platform names are: Interpreter Host CUDA
INFO:jax._src.xla_bridge:Unable to initialize backend 'tpu': module 'jaxlib.xla_extension' has no attribute 'get_tpu_client'
INFO:jax._src.xla_bridge:Unable to initialize backend 'plugin': xla_extension has no attributes named get_plugin_device_client. Compile TensorFlow with //tensorflow/compiler/xla/python:enable_plugin_device set to true (defaults to false) to enable this.
INFO:absl:Initialising environment...
INFO:absl:Environment initialised.
INFO:absl:Device count: 1, process count: 1 (id 0), local device count: 1, devices to be used 

In [6]:
path = "/nfs/nhome/live/aoomerjee/MSc-Thesis/hct/training_runs/LowLevel, {'position_goals': False, 'velocity_goals': 'full', 'distance_reward': 'difference', 'goal_obs': 'concatenate'}, 2023-07-24, 22:19:51/training_params"
from hct.io.model import load

a = load(path)
print(a)

{'morphology': 'ant', 'goal_obs': 'concatenate', 'position_goals': False, 'velocity_goals': 'full', 'goal_root_pos_range': Array([[-3.  ,  3.  ],
       [-3.  ,  3.  ],
       [-0.25,  0.6 ]], dtype=float32), 'goal_root_rot_range': Array([[-3.1415927,  3.1415927],
       [ 0.       ,  3.1415927],
       [-3.1415927,  3.1415927]], dtype=float32), 'goal_root_vel_range': Array([[-10,  10],
       [-10,  10],
       [ -5,   5]], dtype=int32), 'goal_root_ang_range': Array([[-10,  10],
       [-10,  10],
       [ -5,   5]], dtype=int32), 'goalsampler_root_rot_range': Array([[-3.1415927,  3.1415927],
       [ 0.       ,  0.2617994],
       [-3.1415927,  3.1415927]], dtype=float32), 'obs_mask': None, 'action_mask': None, 'distance_reward': 'difference', 'terminate_when_unhealthy': True, 'terminate_when_goal_reached': True, 'healthy_z_range': (0.2, 2.0), 'goal_distance_epsilon': 0.01, 'reset_noise_scale': 0.1, 'backend': 'generalized', 'architecture_configs': {'num_layers': 3, 'd_model': 256, '

2023-07-19 13:15:49.584823: E external/xla/xla/stream_executor/cuda/cuda_driver.cc:268] failed call to cuInit: CUDA_ERROR_NO_DEVICE: no CUDA-capable device is detected
No GPU/TPU found, falling back to CPU. (Set TF_CPP_MIN_LOG_LEVEL=0 and rerun for more info.)


16


In [2]:
from brax.envs.ant import Ant
env2 = Ant()
rng = jax.random.PRNGKey(0)
jit_env_reset = jax.jit(env2.reset)
jit_env_step = jax.jit(env2.step)
state = jit_env_reset(rng)
action = jp.full((8,), -1)
nstate = jit_env_step(state, action)
print(timeit(jit_env_reset, rng)[1])
print(timeit(jit_env_step, state, action)[1])



0.0013747215270996094
0.0019698143005371094


In [3]:
jit_reset, jit_step, reset_states, step_states, reset_times = env.test(iterations=100)


Time to JIT 'reset': 9.265955924987793 seconds
Time to JIT 'step': 12.438810586929321 seconds
Time to call 'reset' after JIT compilation: 0.008304574489593505 seconds
Time to call 'step' after JIT compilation: 0.0008282780647277834 seconds


In [4]:
@jax.jit
def goal_to_state(goal):
    x=goal.x_world
    xd=goal.xd_world
    q, qd = goal.q, goal.qd
    return base.State(q, qd, x, xd, None)


idx = jp.argsort(jp.array(reset_times))[::-1]
goals = [reset_states[i].info['goal'] for i in idx]
rollout = [goal_to_state(reset_states[i].info['goal']) for i in idx]
rollout_cond_u = jp.array([reset_states[i].info['cond'] for i in idx])
rollout_cond = jp.array([jp.count_nonzero(reset_states[i].info['cond'] == 0.09).item() for i in idx])
html_rollout = html.render(env.sys, rollout)
print(html_rollout)
print(rollout_cond_u)
print(goals[-1].g[6:14])
print(rollout[-1].q[7:])
print(env.goalsampler_limit[6:])

<!DOCTYPE html>
<html>

  <head>
    <title>Brax visualizer</title>
    <link rel="shortcut icon" type="image/x-icon" href="/favicon.ico">
  </head>

  <style>
    body {
      margin: 0;
      padding: 0;
    }

    #brax-viewer {
      height: 480px;
      margin: 0;
      padding: 0;
    }
  </style>
  <script async src="https://unpkg.com/es-module-shims@1.6.3/dist/es-module-shims.js"></script>

  <script type="importmap">
    {
      "imports": {
        "three": "https://unpkg.com/three@0.150.1/build/three.module.js",
        "three/addons/": "https://unpkg.com/three@0.150.1/examples/jsm/",
        "lilgui": "https://cdn.jsdelivr.net/npm/lil-gui@0.18.0/+esm",
        "viewer": "https://cdn.jsdelivr.net/gh/google/brax@v0.9.1/brax/visualizer/js/viewer.js"
      }
    }
  </script>

  <script type="application/javascript">
  var system = {"dt": 0.009999999776482582, "gravity": [0.0, 0.0, -9.8100004196167], "viscosity": 0.0, "density": 0.0, "link": {"transform": {"pos": [[0.0, 0.0, 0.

In [12]:
reset_times_ordered = jp.array([reset_times[i] for i in idx])
unique_ints = jp.unique(jp.array(rollout_cond))
averages = {i.item(): jp.mean(reset_times_ordered[jp.where(rollout_cond==i.item())]) for i in unique_ints}
rollout_by_cond = {i.item(): [rollout[j] for j in jp.where(rollout_cond==i.item())[0]] for i in unique_ints}
print(html.render(env.sys, rollout_by_cond[1]))
print(averages)
print(html.render(env.sys.replace(dt=1), rollout_by_cond[0]))

<!DOCTYPE html>
<html>

  <head>
    <title>Brax visualizer</title>
    <link rel="shortcut icon" type="image/x-icon" href="/favicon.ico">
  </head>

  <style>
    body {
      margin: 0;
      padding: 0;
    }

    #brax-viewer {
      height: 480px;
      margin: 0;
      padding: 0;
    }
  </style>
  <script async src="https://unpkg.com/es-module-shims@1.6.3/dist/es-module-shims.js"></script>

  <script type="importmap">
    {
      "imports": {
        "three": "https://unpkg.com/three@0.150.1/build/three.module.js",
        "three/addons/": "https://unpkg.com/three@0.150.1/examples/jsm/",
        "lilgui": "https://cdn.jsdelivr.net/npm/lil-gui@0.18.0/+esm",
        "viewer": "https://cdn.jsdelivr.net/gh/google/brax@v0.9.1/brax/visualizer/js/viewer.js"
      }
    }
  </script>

  <script type="application/javascript">
  var system = {"dt": 0.009999999776482582, "gravity": [0.0, 0.0, -9.8100004196167], "viscosity": 0.0, "density": 0.0, "link": {"transform": {"pos": [[0.0, 0.0, 0.

In [4]:
from hct.envs.tools import timeit
rng = jax.random.PRNGKey(0)
rng, rng1, rng2, rng3, rng4 = jax.random.split(rng, 5)

action0 = jax.random.uniform(rng1, shape=(env.sys.act_size(),), minval=-1, maxval=1)
action1 = jax.random.uniform(rng2, shape=(env.sys.act_size(),), minval=-1, maxval=1)

jit_reset = jax.jit(env.reset)
jit_step = jax.jit(env.step)

reset_state0, reset_time0 = timeit(jit_reset, rng3)
step_state0, step_time0 = timeit(jit_step, reset_state0, action0)
reset_state1, reset_time1 = timeit(jit_reset, rng4)
step_state1, step_time1 = timeit(jit_step, reset_state1, action1)

time_to_jit_reset = reset_time0 - reset_time1
time_to_jit_step = step_time0 - step_time1
time_to_call_reset = reset_time1
time_to_call_step = step_time1

print(f"Time to JIT 'reset': {time_to_jit_reset} seconds")
print(f"Time to JIT 'step': {time_to_jit_step} seconds")
print(f"Time to call 'reset' after JIT compilation: {time_to_call_reset} seconds")
print(f"Time to call 'step' after JIT compilation: {time_to_call_step} seconds")

TypeError: only integer scalar arrays can be converted to a scalar index

In [3]:

rng, rng1, rng2, rng3, rng4 = jax.random.split(rng, 5)
state, time = timeit(jit_reset, rng)
print(time)

NameError: name 'timeit' is not defined

In [33]:

#rng = jax.random.PRNGKey(0)
rng, rng1 = jax.random.split(rng)
state, time = timeit(jit_reset, rng)
print(time)


0.010477781295776367


In [3]:
from brax.kinematics import inverse, world_to_joint



rng = jax.random.PRNGKey(0)
rollout = []
for i in range(100):
    rng, rng1 = jax.random.split(rng)
    state = jit_reset(rng1)
    goal = state.info['goal']
    goal_state = goal_to_state(goal)
    rollout.append(goal_state)

html_rollout = html.render(env.sys.replace(dt=env.dt), rollout)



In [ ]:
print(jax.random.split(rng))

In [5]:
from brax import base
import jax
import jax.numpy as jp
def mul(a, b):
    return jax.tree_map(lambda x, y: x * y, a, b)

a = base.Transform.zero()
print(mul(a,base.Transform(jp.array([1,1,1]), jp.array([1,1,1,1]))))

Transform(pos=Array([0., 0., 0.], dtype=float32), rot=Array([1., 0., 0., 0.], dtype=float32))


In [3]:
import jax
import jax.numpy as jp
rng = jax.random.PRNGKey(0)


[0 1 1 0]


In [7]:
def func():
    print(1)
    return 1

f = jax.jit(func)
a = f()

1


In [6]:
a=f()

In [34]:
rollout_rel_x = []
rollout_rel_xd = []

for state in rollout:
    rollout_rel_x.append(world_to_relative(state.x, env.sys))
    rollout_rel_xd.append(world_to_relative(state.xd, env.sys))

In [15]:
from brax import base
x = base.Transform.zero()
x1 = base.Transform.zero()
x2 = base.Transform.zero()
x3 = base.Transform.zero()


def fun(a,b):
    return a.__sub__(b)
a = jax.tree_map(lambda x,y: jp.stack([x,y]), x, x1)
b = jax.tree_map(lambda x,y: jp.stack([x,y]), x2, x3)
print(fun(x,x1))

Transform(pos=Array([0., 0., 0.], dtype=float32), rot=Array([0., 0., 0., 0.], dtype=float32))


In [27]:
import time

from brax.math import *
from brax.base import Motion, State, System, Transform
from brax.scan import link_types

import jax
import jax.numpy as jp
from typing import Any, Callable, Optional

import types, functools
from multipledispatch import dispatch

@functools.singledispatch
def world_to_relative(t, sys: System, mask_root: bool = False):
    del t, sys
    return NotImplemented

@world_to_relative.register(Transform)
def _(t, sys: System, mask_root: bool = False) -> Transform:
    """Converts a transform in world frame to transform in frame relative to parent link.

    Args:
        t: transform in world frame

    Returns:
        t': transform in relative frame
    """
    link_parents = jp.array(sys.link_parents)
    link_parents = jp.where(link_parents == -1, 0, link_parents)
    root = t.take(0)
    if mask_root:
        root_mask = Transform(jp.array([0.0, 0.0, 1.0]), jp.array([1.0, 1.0, 1.0, 1.0]))
        root = jax.tree_map(lambda x, y: x * y, root, root_mask)
    r = t.take(link_parents)
    return t.vmap(in_axes=(0,0)).to_local(r).index_set(0, root)

@world_to_relative.register(Motion)
def _(m: Motion, sys: System, mask_root: bool = False) -> Motion:
    """Converts a transform in world frame to transform in frame relative to parent link.

    Args:
        t: transform in world frame

    Returns:
        t': transform in relative frame
    """
    link_parents = jp.array(sys.link_parents)
    link_parents = jp.where(link_parents == -1, 0, link_parents)
    root = m.take(0)
    r = m.take(link_parents)
    return m.__sub__(r).index_set(0,root)

world_to_relative_vmap = jax.vmap(world_to_relative, in_axes=(0, None))
env = AntTest()
test_rollout, _ = env.test_rollout()
print(test_rollout[0])

time0 = time.time()
test_rollout_stack = jax.tree_map(lambda l: jp.stack([state for state in l]), test_rollout)    
time1 = time.time()

print(time1-time0)

In [30]:
time0 = time.time()
test_rollout_stack = jax.tree_map(lambda l: jp.stack([state for state in l]), test_rollout)    
time1 = time.time()
print(len)
print(time1-time0)

10.562998294830322


In [35]:
print(len(test_rollout_stack))

451


In [23]:
print(output['rollout_rel_x'][65])

NameError: name 'output' is not defined

In [22]:
a = jp.array(
    [
        [[1,2,3],
        [4,5,6],
        [7,8,9]]
    ,
        [[10,11,12],
        [13,14,15],
        [16,17,18]]
    ]
,dtype = jp.float32)
idx = jp.array([[0,1,1],[1,0,1],[0,0,0]])
print(idx[None, ...].shape)
print(jp.take_along_axis(a, jp.expand_dims(idx, axis=0), axis=0))


(1, 3, 3)
[[[ 1. 11. 12.]
  [13.  5. 15.]
  [ 7.  8.  9.]]]


In [2]:
from hct.envs.tools import world_to_relative
x = env.reset(rng, None).pipeline_state.x
print(x)
print(world_to_relative(x, env.sys))

Transform(pos=Array([[ 0.        ,  0.        ,  0.55      ],
       [ 0.4       ,  0.4       ,  0.55      ],
       [ 0.61612093,  0.61612093,  0.07399213],
       [-0.4       ,  0.4       ,  0.55      ],
       [-0.61612093,  0.61612093,  0.07399213],
       [-0.4       , -0.4       ,  0.55      ],
       [-0.61612093, -0.61612093,  0.07399213],
       [ 0.4       , -0.4       ,  0.55      ],
       [ 0.61612093, -0.61612093,  0.07399213]], dtype=float32), rot=Array([[ 1.        ,  0.        ,  0.        ,  0.        ],
       [ 1.        ,  0.        ,  0.        ,  0.        ],
       [ 0.87758255, -0.33900505,  0.33900505,  0.        ],
       [ 1.        ,  0.        ,  0.        ,  0.        ],
       [ 0.87758255, -0.33900505, -0.33900505,  0.        ],
       [ 1.        ,  0.        ,  0.        ,  0.        ],
       [ 0.87758255,  0.33900505, -0.33900505,  0.        ],
       [ 1.        ,  0.        ,  0.        ,  0.        ],
       [ 0.87758255,  0.33900505,  0.33900505

In [5]:
env = Ant()
output = env.get_limb_ranges()
print(output['html'])

FileNotFoundError: [Errno 2] No such file or directory: '/nfs/nhome/live/aoomerjee/MSc-Thesis/hct/envs/assets/ant_v2.xml'

In [2]:
print(output['pos_ranges'][0][2])
print(output['pos_ranges'][0][4])
print(output['pos_ranges'][0][6])
print(output['pos_ranges'][0][8])
print(output['html'])

[ 0.1368081   0.1368081  -0.53157055]
[ 0.13680622  0.13680623 -0.5315716 ]
[ 0.13680622  0.13680623 -0.5315716 ]
[ 0.09961223  0.09961222 -0.5478641 ]
<!DOCTYPE html>
<html>

  <head>
    <title>Brax visualizer</title>
    <link rel="shortcut icon" type="image/x-icon" href="/favicon.ico">
  </head>

  <style>
    body {
      margin: 0;
      padding: 0;
    }

    #brax-viewer {
      height: 480px;
      margin: 0;
      padding: 0;
    }
  </style>
  <script async src="https://unpkg.com/es-module-shims@1.6.3/dist/es-module-shims.js"></script>

  <script type="importmap">
    {
      "imports": {
        "three": "https://unpkg.com/three@0.150.1/build/three.module.js",
        "three/addons/": "https://unpkg.com/three@0.150.1/examples/jsm/",
        "lilgui": "https://cdn.jsdelivr.net/npm/lil-gui@0.18.0/+esm",
        "viewer": "https://cdn.jsdelivr.net/gh/google/brax@v0.9.1/brax/visualizer/js/viewer.js"
      }
    }
  </script>

  <script type="application/javascript">
  var syste

In [10]:
from hct.envs.tools import world_to_relative
rng = jax.random.PRNGKey(0)
r = env.reset(rng, limit_id=0)
state = r.pipeline_state
print(state.x.pos)
print(world_to_relative(state.x, env.sys).pos)

print(jp.array(env.sys.link_parents))

[[ 0.          0.          0.        ]
 [ 0.4732051   0.27320507  0.        ]
 [ 0.94641024  0.4        -0.28284276]
 [-0.27320507  0.4732051   0.        ]
 [-0.32328027  0.6600884  -0.5315705 ]
 [-0.4732051  -0.27320507  0.        ]
 [-0.6600884  -0.32328027 -0.5315705 ]
 [ 0.27320507 -0.4732051   0.        ]
 [ 0.4        -0.94641024 -0.28284276]]
[[ 0.          0.          0.        ]
 [ 0.4732051   0.27320507  0.        ]
 [ 0.34641024  0.34641027 -0.2828428 ]
 [-0.27320507  0.4732051   0.        ]
 [-0.13680808  0.13680811 -0.53157055]
 [-0.4732051  -0.27320507  0.        ]
 [-0.13680811 -0.13680808 -0.53157055]
 [ 0.27320507 -0.4732051   0.        ]
 [ 0.34641027 -0.34641024 -0.2828428 ]]
[-1  0  1  0  3  0  5  0  7]


In [15]:
def w(t, sys, mask_root: bool = False) -> Transform:
    """Converts a transform in world frame to transform in frame relative to parent link.

    Args:
        t: transform in world frame

    Returns:
        t': transform in relative frame
    """
    link_parents = jp.array(sys.link_parents)
    link_parents = jp.where(link_parents == -1, 0, link_parents)
    print(link_parents)
    root = t.take(0)
    if mask_root:
        root_mask = Transform(jp.array([0.0, 0.0, 1.0]), jp.array([1.0, 1.0, 1.0, 1.0]))
        root = jax.tree_map(lambda x, y: x * y, root, root_mask)
    r = t.take(link_parents)
    print(r)
    return t.vmap(in_axes=(0,0)).to_local(r).index_set(0, root)

w(state.x, env.sys).pos

[0 0 1 0 3 0 5 0 7]
Transform(pos=Array([[ 0.        ,  0.        ,  0.        ],
       [ 0.        ,  0.        ,  0.        ],
       [ 0.4732051 ,  0.27320507,  0.        ],
       [ 0.        ,  0.        ,  0.        ],
       [-0.27320507,  0.4732051 ,  0.        ],
       [ 0.        ,  0.        ,  0.        ],
       [-0.4732051 , -0.27320507,  0.        ],
       [ 0.        ,  0.        ,  0.        ],
       [ 0.27320507, -0.4732051 ,  0.        ]], dtype=float32), rot=Array([[ 1.        ,  0.        ,  0.        ,  0.        ],
       [ 1.        ,  0.        ,  0.        ,  0.        ],
       [ 0.9659259 ,  0.        ,  0.        , -0.25881907],
       [ 1.        ,  0.        ,  0.        ,  0.        ],
       [ 0.9659259 ,  0.        ,  0.        , -0.25881907],
       [ 1.        ,  0.        ,  0.        ,  0.        ],
       [ 0.9659259 ,  0.        ,  0.        , -0.25881907],
       [ 1.        ,  0.        ,  0.        ,  0.        ],
       [ 0.9659259 ,  0. 

Array([[ 0.        ,  0.        ,  0.        ],
       [ 0.4732051 ,  0.27320507,  0.        ],
       [ 0.34641024,  0.34641027, -0.2828428 ],
       [-0.27320507,  0.4732051 ,  0.        ],
       [-0.13680808,  0.13680811, -0.53157055],
       [-0.4732051 , -0.27320507,  0.        ],
       [-0.13680811, -0.13680808, -0.53157055],
       [ 0.27320507, -0.4732051 ,  0.        ],
       [ 0.34641027, -0.34641024, -0.2828428 ]], dtype=float32)

In [17]:
print(env.sys.dof.limit[0])
print(env.sys.dof.limit[1])

[      -inf       -inf       -inf       -inf       -inf       -inf
 -0.5235988  0.5235988 -0.5235988 -1.2217305 -0.5235988 -1.2217305
 -0.5235988  0.5235988]
[       inf        inf        inf        inf        inf        inf
  0.5235988  1.2217305  0.5235988 -0.5235988  0.5235988 -0.5235988
  0.5235988  1.2217305]


In [4]:
env = Ant()

jit_env_reset = jax.jit(env.reset)
jit_env_step = jax.jit(env.step)
jit_inference_fn = jax.random.uniform

rollout = []
rng = jax.random.PRNGKey(seed=1)
state = jit_env_reset(rng=rng)
for _ in range(1000):
  rollout.append(state.pipeline_state)
  act_rng, rng = jax.random.split(rng)
  act = jit_inference_fn(act_rng, shape=(8,), minval = -1,maxval=1)
  state = jit_env_step(state, act)

HTML(html.render(env.sys.replace(dt=env.dt), rollout))


In [5]:
print(html.render(env.sys.replace(dt=env.dt), rollout))

<!DOCTYPE html>
<html>

  <head>
    <title>Brax visualizer</title>
    <link rel="shortcut icon" type="image/x-icon" href="/favicon.ico">
  </head>

  <style>
    body {
      margin: 0;
      padding: 0;
    }

    #brax-viewer {
      height: 480px;
      margin: 0;
      padding: 0;
    }
  </style>
  <script async src="https://unpkg.com/es-module-shims@1.6.3/dist/es-module-shims.js"></script>

  <script type="importmap">
    {
      "imports": {
        "three": "https://unpkg.com/three@0.150.1/build/three.module.js",
        "three/addons/": "https://unpkg.com/three@0.150.1/examples/jsm/",
        "lilgui": "https://cdn.jsdelivr.net/npm/lil-gui@0.18.0/+esm",
        "viewer": "https://cdn.jsdelivr.net/gh/google/brax@v0.9.1/brax/visualizer/js/viewer.js"
      }
    }
  </script>

  <script type="application/javascript">
  var system = {"dt": 0.04999999701976776, "gravity": [0.0, 0.0, 0.0], "viscosity": 0.0, "density": 0.0, "link": {"transform": {"pos": [[0.0, 0.0, 0.0], [0.2000000

In [5]:
x = state.pipeline_state.x

l = jp.array(env.sys.link_parents)

root = x.take(0)
root_mask = jp.array([0.0, 0.0, 1.0]), jp.array([1.0, 1.0, 1.0, 1.0])
root = root.__mul__(root_mask)

TypeError: unsupported operand type(s) for *: 'ArrayImpl' and 'tuple'

In [ ]:
kwargs = {'debug': True}
env = Ant(**kwargs)

jit_env_reset = jax.jit(env.reset)
jit_env_step = jax.jit(env.step)
jit_inference_fn = jax.random.uniform

rollout = []
rng = jax.random.PRNGKey(seed=1)
state = jit_env_reset(rng=rng)
for _ in range(1000):
  rollout.append(state.pipeline_state)
  act_rng, rng = jax.random.split(rng)
  act = jit_inference_fn(act_rng, shape=(8,), minval = -1,maxval=1)
  state = jit_env_step(state, act)

HTML(html.render(env.sys.replace(dt=env.dt), rollout))

In [3]:
print(html.render(env.sys.replace(dt=env.dt), rollout))


<!DOCTYPE html>
<html>

  <head>
    <title>Brax visualizer</title>
    <link rel="shortcut icon" type="image/x-icon" href="/favicon.ico">
  </head>

  <style>
    body {
      margin: 0;
      padding: 0;
    }

    #brax-viewer {
      height: 480px;
      margin: 0;
      padding: 0;
    }
  </style>
  <script async src="https://unpkg.com/es-module-shims@1.6.3/dist/es-module-shims.js"></script>

  <script type="importmap">
    {
      "imports": {
        "three": "https://unpkg.com/three@0.150.1/build/three.module.js",
        "three/addons/": "https://unpkg.com/three@0.150.1/examples/jsm/",
        "lilgui": "https://cdn.jsdelivr.net/npm/lil-gui@0.18.0/+esm",
        "viewer": "https://cdn.jsdelivr.net/gh/google/brax@v0.9.1/brax/visualizer/js/viewer.js"
      }
    }
  </script>

  <script type="application/javascript">
  var system = {"dt": 0.04999999701976776, "gravity": [0.0, 0.0, -9.8100004196167], "viscosity": 0.0, "density": 0.0, "link": {"transform": {"pos": [[0.0, 0.0, 0.0

In [4]:
s = state.pipeline_state
from brax.geometry import contact


f = lambda y: contact(env.sys, y)
x = [f(s.x) for s in rollout]
print(x)


[Contact(pos=Array([[ 0.        ,  0.        ,  0.15      ],
       [ 0.4       ,  0.4       ,  0.23500001],
       [ 0.61612093,  0.61612093, -0.00300393],
       [-0.4       ,  0.4       ,  0.23500001],
       [-0.61612093,  0.61612093, -0.00300393],
       [-0.4       , -0.4       ,  0.23500001],
       [-0.61612093, -0.61612093, -0.00300393],
       [ 0.4       , -0.4       ,  0.23500001],
       [ 0.61612093, -0.61612093, -0.00300393]], dtype=float32), normal=Array([[0., 0., 1.],
       [0., 0., 1.],
       [0., 0., 1.],
       [0., 0., 1.],
       [0., 0., 1.],
       [0., 0., 1.],
       [0., 0., 1.],
       [0., 0., 1.],
       [0., 0., 1.]], dtype=float32), penetration=Array([-0.3       , -0.47000003,  0.00600787, -0.47000003,  0.00600787,
       -0.47000003,  0.00600787, -0.47000003,  0.00600787], dtype=float32), friction=Array([1., 1., 1., 1., 1., 1., 1., 1., 1.], dtype=float32), elasticity=Array([0., 0., 0., 0., 0., 0., 0., 0., 0.], dtype=float32), solver_params=Array([[2.0

In [5]:
for i in x:
    print(i.pos)

[[ 0.          0.          0.15      ]
 [ 0.4         0.4         0.23500001]
 [ 0.61612093  0.61612093 -0.00300393]
 [-0.4         0.4         0.23500001]
 [-0.61612093  0.61612093 -0.00300393]
 [-0.4        -0.4         0.23500001]
 [-0.61612093 -0.61612093 -0.00300393]
 [ 0.4        -0.4         0.23500001]
 [ 0.61612093 -0.61612093 -0.00300393]]
[[-1.2581423e-03 -6.7540961e-03  1.6022289e-01]
 [ 3.5754704e-01  4.2954671e-01  2.4016196e-01]
 [ 5.2488565e-01  6.5746725e-01 -4.8125461e-03]
 [-3.7900928e-01  4.1073301e-01  2.4504125e-01]
 [-5.3413022e-01  6.0455954e-01 -9.1087595e-03]
 [-4.0272155e-01 -4.0405205e-01  2.5031447e-01]
 [-5.9406185e-01 -5.7505482e-01 -1.7504171e-03]
 [ 3.9768755e-01 -4.0686163e-01  2.4515831e-01]
 [ 5.7906222e-01 -6.2058043e-01 -5.1809102e-04]]
[[ 1.2500003e-02 -1.6772561e-02  1.8308216e-01]
 [ 3.1810039e-01  4.5786375e-01  2.6954532e-01]
 [ 3.7814853e-01  6.1616683e-01 -3.3164769e-04]
 [-3.6316085e-01  3.9156890e-01  2.8072065e-01]
 [-4.3259227e-01  4.881

In [39]:
arr = jp.array([2,4,6,8])
for i in range(10): 
    rng, rng1, rng2 = jax.random.split(rng, 3)
    n = jax.random.choice(rng2, jp.array(range(0,len(arr)+1)))
    r = jax.random.choice(rng1, arr, shape=(n,), replace = False)
    r = jp.sort(r)
    print(r)

print(arr[r])

[]
[2]
[4 6 8]
[2 4 6 8]
[2 4 6]
[2 4 6 8]
[4 8]
[]
[4 6 8]
[6 8]
[8 8]


In [ ]:
import numpy as np
from brax.base import State
env = Ant()
goalconstructor = GoalConstructor(env.sys, configs = {})

q = env.sys.init_q 
qd = jp.zeros(env.sys.qd_size())
rng = jax.random.PRNGKey(seed=np.random.randint(0,1000))
@jax.jit
def f(rng):
    pipeline_state = env.pipeline_init(q, qd)
    
    # Sample and set goal
    goal = goalconstructor.sample_goal(rng, pipeline_state)

    """print(goal.q)
    print(goalconstructor.dof_limits)"""

    state = State(
        q = goal.q,
        qd = goal.qd,
        x = goal.x,
        xd = goal.xd,
        contact=None
    )
    return state

rollout = []
for r in range(10):
    rng, rng1 = jax.random.split(rng)
    rollout.append(f(rng1))

display(HTML(html.render(env.sys.replace(dt=env.dt), rollout)))

#self.goalconstructor.sample_goal()

In [ ]:
display(HTML(html.render(env.sys.replace(dt=env.dt), rollout)))
